# RNA-seq Analysis Notebook
## Overview
This notebook contains a guided walkthrough to building a simple pipeline for analysis of an RNA-seq dataset.

The pipeline described here consists of the following steps:
1. **Download** an RNA-seq dataset (ARCHS4)
2. **Normalize expression** data (Variance Stabilizing Transformation)
3. Perform **Dimensionality Reduction** (PCA and t-SNE)
4. Visualize the dataset as a **clustered heatmap** (Clustergrammer)
5. Perform **Differential Gene Expression Analysis** (limma and CD)
6. Perform **Enrichment analysis** (Enrichr)

## Load Packages

In [1]:
%%capture
# Python packages
import sys
import rpy2
import numpy as np
from plotly.offline import init_notebook_mode

# Initialize Plotly and R magic
%load_ext rpy2.ipython
%R require(DESeq2)
%R require(limma)
%R require(edgeR)

# Custom scripts
sys.path.append('scripts')
import archs4
# from plots import *
from signature import *

## 1. Download RNA-seq Dataset
Here we download RNA-seq datasets processed by ARCHS4.

The following datasets are suggested:
* *Homo sapiens* datasets:
    * **Nucleotide stress induction of HEXIM1 suppresses melanoma by modulating cancer cell-specific gene transcription** (GSE68053_GPL16791)
    * **Potent and targeted activation of HIV-1 using the CRISPR/Cas9 activator Complex** (GSE72259_GPL16791)
    * **EZH2 and BCL6 cooperate to assemble CBX8-BCOR Polycomb complex to repress bivalent promoters, mediate germinal center formation and promote lymphomagenesis** (GSE73109_GPL11154)
    
   
* *Mus musculus* datasets:
    * **HEB associates with PRC2 and SMAD2/3 to regulate developmental fates** (GSE60285_GPL13112)
    * **Transcriptomic signatures uncover gene expression differences associated with the development of phenotypic differences in serial organs** (GSE72468_GPL11154)
    * **OSKM induce extraembryonic endoderm stem (iXEN) cells in parallel to iPS cells** (GSE77550_GPL17021)

A full list of datasets processed by ARCHS4 is available in the *archs4_datasets.txt* file.

In [131]:
# Fetch dataset from ARCHS4 server.  Insert code specified in brackets to extract specified dataset
rawcount_dataframe, sample_metadata_dataframe = archs4.fetch_dataset('GSE72468_GPL11154')

In [132]:
# Display the raw readcount dataframe
rawcount_dataframe.head()

GSM1866102  GSM1866103  GSM1866104  GSM1866105  GSM1866106  \
ID_REF                                                               
A1BG           305         363         183         380         238   
A1CF             3           4          18          29          27   
A2M          35171       38510        3155        4621       19653   
A2ML1          645         544         112          90          82   
A2MP1           18          10          13          11          26   

        GSM1866107  GSM1866108  GSM1866109  GSM1866110  GSM1866111  \
ID_REF                                                               
A1BG           430          38          43          18          31   
A1CF            28           4          10           7          10   
A2M           4530           1           1          27          31   
A2ML1          305           5           2           0           5   
A2MP1           21           0           0           1           1   

        GSM1866112  GSM1866113  GSM1866114  GSM1866115  GSM1866138  
ID_REF                                                              
A1BG           128         178         111         142         256  
A1CF             8           9          28           8          12  
A2M              0           0           0           1        7717  
A2ML1            5           5           7          11          94  
A2MP1            0           0           0           2          37

In [133]:
# Display the sample metadata dataframe
sample_metadata_dataframe

cell line               tissue
GSM1866102                     NaN  Gliobmastoma biopsy
GSM1866103                     NaN  Gliobmastoma biopsy
GSM1866104                     NaN  Gliobmastoma biopsy
GSM1866105                     NaN  Gliobmastoma biopsy
GSM1866106                     NaN  Gliobmastoma biopsy
GSM1866107                     NaN  Gliobmastoma biopsy
GSM1866108  Gliobmastoma cell line                  NaN
GSM1866109  Gliobmastoma cell line                  NaN
GSM1866110  Gliobmastoma cell line                  NaN
GSM1866111  Gliobmastoma cell line                  NaN
GSM1866112  Gliobmastoma cell line                  NaN
GSM1866113  Gliobmastoma cell line                  NaN
GSM1866114  Gliobmastoma cell line                  NaN
GSM1866115  Gliobmastoma cell line                  NaN
GSM1866138                     NaN  Gliobmastoma biopsy

## 2. Normalization

Before proceeding with the analysis, we normalize the raw readcount dataset using the **Variance Stabilizing Transformation** (VST) method, from the *DESeq2* package in R.

In [134]:
# Push the dataset to R
%Rpush rawcount_dataframe

# Normalize
%R vst_dataframe <- as.data.frame(varianceStabilizingTransformation(as.matrix(rawcount_dataframe)))

# Pull the dataset from R
%Rpull vst_dataframe

# Display
vst_dataframe.head()

GSM1866102  GSM1866103  GSM1866104  GSM1866105  GSM1866106  GSM1866107  \
A1BG     8.077563    8.068407    8.172482    8.818753    8.123599    8.789892   
A1CF     2.288148    2.379400    4.938582    5.202222    5.082964    4.963302   
A2M     14.913209   14.783662   12.267945   12.415260   14.477936   12.179322   
A2ML1    9.150746    8.647410    7.472302    6.767060    6.611454    8.297819   
A2MP1    4.193430    3.285175    4.513203    3.952836    5.032604    4.585988   

       GSM1866108  GSM1866109  GSM1866110  GSM1866111  GSM1866112  GSM1866113  \
A1BG     5.573278    5.950002    5.243523    5.363837    6.382259    6.590261   
A1CF     2.828367    4.024439    4.020937    3.901485    2.892051    2.828199   
A2M      1.708043    1.804432    5.796069    5.363837    0.377510    0.377510   
A2ML1    3.057115    2.327004    0.377510    3.109695    2.445213    2.288924   
A2MP1    0.377510    0.377510    2.054782    1.739224    0.377510    0.377510   

       GSM1866114  GSM1866115  GSM1866138  
A1BG     6.005235    6.486188    8.513798  
A1CF     4.174631    2.862219    4.287165  
A2M      0.377510    1.350133   13.417692  
A2ML1    2.635795    3.195130    7.085840  
A2MP1    0.377510    1.729218    5.781922

## 3. Dimensionality Reduction

### 3.1 PCA
First, we perform a **Principal Components Analysis** (PCA) on the dataset, reducing it to two or three dimensions.  To achieve this, use the PCA function in the Python package *sklearn* - reference code is available at http://scikit-learn.org/stable/modules/generated/sklearn.decomposition.PCA.html.

Before starting, in order to reduce computation time, we take a subset of the top N (e.g. 5000) most variable genes.

In [135]:
# Get gene by variance
geneVariance = vst_dataframe.apply(np.var, 1)

In [136]:
# Get top N genes
N = 5000
topGenes = geneVariance.nlargest(N).index

# Get subset
vst_dataframe_subset = vst_dataframe.loc[topGenes]

In [137]:
# Activate Plotly
init_notebook_mode()

# Take

# Insert code to perform PCA here
from sklearn.decomposition import PCA
pca = PCA(n_components=3)
pca.fit(vst_dataframe_subset)

PCA(copy=True, iterated_power='auto', n_components=3, random_state=None,
  svd_solver='auto', tol=0.0, whiten=False)

In [ ]:
import plots
reload(plots)
# Plot using one of the following functions
# plots.plot_2d_scatter(pca.components_[0], pca.components_[1], text=sample_metadata_dataframe.index.tolist(), color_by=sample_metadata_dataframe['developmental stage'])
plots.plot_3d_scatter(pca.components_[0],
                      pca.components_[1],
                      pca.components_[2],
                      text=sample_metadata_dataframe.index.tolist(),
                      color_by=sample_metadata_dataframe['cell line'])

### 3.2 t-SNE
Second, we perform **t-Distributed Stochastic Neighbor Embedding** (t-SNE) on the dataset, reducing it to two or three dimensions.  To achieve this, use the tsne function in the Python package *sklearn* - reference code is available at http://scikit-learn.org/stable/modules/generated/sklearn.manifold.TSNE.html.

In [98]:
# Insert code to perform t-SNE here
from sklearn.manifold import TSNE
model = TSNE(n_components=2, random_state=0)
# np.set_printoptions(suppress=True)
model.fit_transform(vst_dataframe.T)

array([[ 0.00017591,  0.00004004],
       [ 0.00009758,  0.00022303],
       [ 0.00018607, -0.00009721],
       [ 0.00009478, -0.000015  ],
       [-0.00001023,  0.00004108],
       [ 0.00001455,  0.00014476],
       [ 0.00007605,  0.00001208],
       [ 0.00004433,  0.00003334],
       [ 0.00014898, -0.00002041],
       [ 0.00003135, -0.00008528],
       [-0.00025348,  0.00006502],
       [ 0.00008628, -0.00007407],
       [ 0.00022596, -0.00014453],
       [ 0.0000047 , -0.00001867],
       [ 0.00015283,  0.00014643],
       [ 0.00001555,  0.00003786],
       [-0.00008801, -0.00019705],
       [-0.00003458,  0.0000157 ]])

In [96]:
# Plot using one of the following functions
# plot_2d_scatter(x, y, sample_names)
plots.plot_3d_scatter(pd.DataFrame(model.embedding_)[0],
                pd.DataFrame(model.embedding_)[1],
                pd.DataFrame(model.embedding_)[2],
                text=sample_metadata_dataframe.index.tolist(),
                color_by=sample_metadata_dataframe['cell line'])

## 4. Clustergrammer
Next, we generate an **interactive clustered heatmap** to explore the most variable genes in the dataset.  To achieve this, we use the *Clustergrammer* package - reference code is available at http://clustergrammer.readthedocs.io/clustergrammer_widget.html#clustergrammer-widget-workflow-example.

In [107]:
reload(plots)

<module 'plots' from 'scripts/plots.py'>

In [116]:
# Insert code to create widget here
# Steps: (1) create Network object, (2) load dataframe
#        (3) Z-score normalize the rows, (4) filter top 500 genes by variance
#        (5) cluster the heatmap, (6) display the widget
from clustergrammer_widget import *
net = Network(clustergrammer_widget)
net.load_df(vst_dataframe)
net.normalize(axis='col', norm_type='zscore', keep_orig=True)
net.filter_N_top('row', 500, 'var')
net.add_cats('col', plots.get_clustergrammer_cats(sample_metadata_dataframe))
net.cluster()
net.widget()

## 5. Differential Expression Analysis
Here we identify **Differentially Expressed Genes** (DEGs) using two approaches: limma and Characteristic Direction.  

To achieve this, we need to select two sets of samples:
* a group of *experimental / treated samples*
* a second group of *control / untreated samples*

### 1. limma
First, we perform the analysis using the *limma* R package.  Reference here https://bioconductor.org/packages/release/bioc/html/limma.html.

In [35]:
sample_metadata_dataframe

developmental stage genotype individual strain  \
GSM1981216              ED14.5       WT       ind1    CD1   
GSM1981217              ED15.0       WT       ind2    CD1   
GSM1981218              ED15.5       WT       ind3    CD1   
GSM1981219              ED16.0       WT       ind4    CD1   
GSM1981220              ED16.5       WT       ind5    CD1   
GSM1981221              ED17.0       WT       ind6    CD1   
GSM1981222              ED17.5       WT       ind7    CD1   
GSM1981223              ED18.0       WT       ind8    CD1   
GSM1981224              ED14.5       WT       ind1    CD1   
GSM1981225              ED15.0       WT       ind2    CD1   
GSM1981226              ED15.5       WT       ind3    CD1   
GSM1981227              ED16.0       WT       ind4    CD1   
GSM1981228              ED16.5       WT       ind5    CD1   
GSM1981229              ED17.0       WT       ind6    CD1   
GSM1981230              ED17.5       WT       ind7    CD1   
GSM1981231              ED18.0       WT       ind8    CD1   

                                                       tissue  
GSM1981216  upper tooth germ (the left and right first mol...  
GSM1981217  upper tooth germ (the left and right first mol...  
GSM1981218  upper tooth germ (the left and right first mol...  
GSM1981219  upper tooth germ (the left and right first mol...  
GSM1981220  upper tooth germ (the left and right first mol...  
GSM1981221  upper tooth germ (the left and right first mol...  
GSM1981222  upper tooth germ (the left and right first mol...  
GSM1981223  upper tooth germ (the left and right first mol...  
GSM1981224  lower tooth germ (the left and right first mol...  
GSM1981225  lower tooth germ (the left and right first mol...  
GSM1981226  lower tooth germ (the left and right first mol...  
GSM1981227  lower tooth germ (the left and right first mol...  
GSM1981228  lower tooth germ (the left and right first mol...  
GSM1981229  lower tooth germ (the left and right first mol...  
GSM1981230  lower tooth germ (the left and right first mol...  
GSM1981231  lower tooth germ (the left and right first mol...

In [36]:
# Run limma using a Python wrapper
limma_dataframe = compute_signature(rawcount_dataframe,
                                    method = 'limma',
                                    experimental_samples = ['GSM1981216', 'GSM1981217', 'GSM1981218'], # insert list of experimental sample names
                                    control_samples = ['GSM1981219', 'GSM1981220', 'GSM1981221'],# insert list of control sample names
                                    )

/Users/denis/my-venv/lib/python2.7/site-packages/rpy2/rinterface/__init__.py:185: RRuntimeWarning:

Loading required package: edgeR




In [37]:
# Explore results
limma_dataframe.head()

logFC   AveExpr         t   P.Value  adj.P.Val         B
RAET1D        -4.657152  0.478840 -3.032262  0.008340        1.0 -4.588813
3110070M22RIK  2.302446  1.151877  2.536445  0.022697        1.0 -4.588836
GM10039        5.470902  3.417453  1.602776  0.129661        1.0 -4.588993
GM13139       -2.302278  1.525164 -2.274218  0.037942        1.0 -4.589118
GM7879         4.566049  0.527126  2.776792  0.014021        1.0 -4.589506

##### Volcano Plot
The Volcano plot is a common way to display results of a differential gene expression analysis.  It displays logFC on the x axis and log10(P-value) on the Y axis.

In [40]:
plot_2d_scatter(x = limma_dataframe['logFC'],
                y = -np.log10(limma_dataframe['P.Value']),
                text = '',
                xlab = '',
                ylab='')

##### MA Plot
The MA plot is a second common way to display results of a differential gene expression analysis.  It displays average normalized expression on the x axis and logFC on the Y axis.

In [42]:
plot_2d_scatter(x = limma_dataframe['AveExpr'],
                y = limma_dataframe['logFC'],
                text = '',
                xlab = '',
                ylab='')

### 2. Characteristic Direction
Second, we calculate a differential gene expression signature using the *Characteristic Direction* method, which has been shown to outperform other methods to identify DEGs in the context of transcription factor (TF) and drug perturbation responses (Clark et al, 2013, [link](https://bmcbioinformatics.biomedcentral.com/articles/10.1186/1471-2105-15-79)).

In [43]:
# Run CD using a Python wrapper
cd_dataframe = compute_signature(rawcount_dataframe,
                                 method = 'CD',
                                 experimental_samples = ['GSM1981216', 'GSM1981217', 'GSM1981218'], # insert list of experimental sample names
                                 control_samples = ['GSM1981219', 'GSM1981220', 'GSM1981221'],# insert list of control sample names
                                 )

In [44]:
# Explore results
cd_dataframe.head()

CD
GM14288    0.083383
RPL14-PS1 -0.082820
GM13691   -0.082146
RPS24-PS3  0.079338
GM6768     0.075903

## 6. Enrichment Analysis
We now use the differential gene expression signature computed with CD and perform **enrichment analysis** on the top most overexpressed and underexpressed genes using the *Enrichr* API.

Reference on how to use the API in Python here http://amp.pharm.mssm.edu/Enrichr/help#api.

In [50]:
# Write code to upload gene lists to the Enrichr API
# Steps: (1) sort the genes by the CD value, (2) take the top 500 top and bottom genes,
# (3) perform POST request as shown in the manual.

up_genes = cd_dataframe.nlargest(500, 'CD').index
dn_genes = cd_dataframe.nsmallest(500, 'CD').index

In [51]:
import json
import requests


ENRICHR_URL = 'http://amp.pharm.mssm.edu/Enrichr/addList'
genes_str = '\n'.join(up_genes)
description = 'Example gene list'
payload = {
    'list': (None, genes_str),
    'description': (None, description)
}

response = requests.post(ENRICHR_URL, files=payload)
if not response.ok:
    raise Exception('Error analyzing gene list')

data = json.loads(response.text)
print(data)


{u'userListId': 4843663, u'shortId': u'2dhpb'}


Once the gene list has been submitted, you can view the enrichment results by appending the 'shortId' at the end of the following URL: http://amp.pharm.mssm.edu/Enrichr/enrich?dataset=.

## 7. Small Molecole Query
Finally, we use the differential gene expression signature computed with CD to identify **small molecules which mimic or reverse** the observed pattern using the *L1000CDS<sup>2</sup>* API.

Reference on how to use the API in Python here http://amp.pharm.mssm.edu/L1000CDS2/help/#api.

In [54]:
# Write code to upload signature to L1000CDS2 API
### "Gene-set search" 
# Steps: (1) sort the genes by the CD value, (2) take the top 500 top and bottom genes,
# (3) perform POST request as shown in the manual (gene-set search example).

import requests
import json
url = 'http://amp.pharm.mssm.edu/L1000CDS2/query'

def upperGenes(genes):
    # The app uses uppercase gene symbols. So it is crucial to perform upperGenes() step.
    return [gene.upper() for gene in genes]

# gene-set search example
data = {"upGenes":up_genes,
"dnGenes":dn_genes}
data['upGenes'] = upperGenes(data['upGenes'])
data['dnGenes'] = upperGenes(data['dnGenes'])
config = {"aggravate":True,"searchMethod":"geneSet","share":True,"combination":True,"db-version":"latest"}
metadata = [{"key":"Tag","value":"gene-set python example"},{"key":"Cell","value":"MCF7"}]
payload = {"data":data,"config":config,"meta":metadata}
headers = {'content-type':'application/json'}
r = requests.post(url,data=json.dumps(payload),headers=headers)
resGeneSet = r.json()
resGeneSet['shareId']

u'596d4304b09d47a600bced96'

Once the gene list has been submitted, you can view the results by appending the 'shareId' at the end of the following URL: http://amp.pharm.mssm.edu/L1000CDS2/#/result/.